In [1]:
# 查看当前挂载的数据集目录, 该目录下的变更重启环境后会自动还原
# View dataset directory. 
# This directory will be recovered automatically after resetting environment. 
!ls /home/aistudio/data

data173448


In [2]:
# 查看工作区文件, 该目录下的变更将会持久保存. 请及时清理不必要的文件, 避免加载过慢.
# View personal work directory. 
# All changes under this directory will be kept even after reset. 
# Please clean unnecessary files in time to speed up environment loading. 
!ls /home/aistudio/work

PaddleOCR


In [ ]:
# 如果需要进行持久化安装, 需要使用持久化路径, 如下方代码示例:
# If a persistence installation is required, 
# you need to use the persistence path as the following: 
!mkdir /home/aistudio/external-libraries
!pip install beautifulsoup4 -t /home/aistudio/external-libraries

In [3]:
# 同时添加如下代码, 这样每次环境(kernel)启动的时候只要运行下方代码即可: 
# Also add the following code, 
# so that every time the environment (kernel) starts, 
# just run the following code: 
import sys 
sys.path.append('/home/aistudio/external-libraries')

下载paddleocr

In [40]:
%cd ~/work
!git clone https://gitee.com/paddlepaddle/PaddleOCR.git --depth=1


/home/aistudio/work
正克隆到 'PaddleOCR'...
remote: Enumerating objects: 1804, done.
remote: Counting objects: 100% (1804/1804), done.
remote: Compressing objects: 100% (1540/1540), done.
remote: Total 1804 (delta 432), reused 1090 (delta 205), pack-reused 0
接收对象中: 100% (1804/1804), 118.80 MiB | 8.42 MiB/s, 完成.
处理 delta 中: 100% (432/432), 完成.
检查连接... 完成。
正在检出文件: 100% (1522/1522), 完成.


请点击[此处](https://ai.baidu.com/docs#/AIStudio_Project_Notebook/a38e5576)查看本环境基本用法.  <br>
Please click [here ](https://ai.baidu.com/docs#/AIStudio_Project_Notebook/a38e5576) for more detailed instructions. 

cd到paddkeocr文件夹并安装需要的环境

In [42]:
!cd ~/work/PaddleOCR && pip install -r requirements.txt 

Looking in indexes: https://pypi.tuna.tsinghua.edu.cn/simple


解压数据集

In [ ]:
%cd ~/data/data173448/
!unzip -d /home/aistudio/work/PaddleOCR/data train_images.zip
!unzip -d /home/aistudio/work/PaddleOCR/data test_images.zip


/home/aistudio/data/data173448
Archive:  train_images.zip
   creating: /home/aistudio/work/PaddleOCR/data/train_images/
  inflating: /home/aistudio/work/PaddleOCR/data/train_images/9733.jpg  
  inflating: /home/aistudio/work/PaddleOCR/data/train_images/14147.jpg  
  inflating: /home/aistudio/work/PaddleOCR/data/train_images/63.jpg  
  inflating: /home/aistudio/work/PaddleOCR/data/train_images/6400.jpg  
  inflating: /home/aistudio/work/PaddleOCR/data/train_images/34297.jpg  
  inflating: /home/aistudio/work/PaddleOCR/data/train_images/42301.jpg  
  inflating: /home/aistudio/work/PaddleOCR/data/train_images/24084.jpg  
  inflating: /home/aistudio/work/PaddleOCR/data/train_images/13628.jpg  
  inflating: /home/aistudio/work/PaddleOCR/data/train_images/23933.jpg  
  inflating: /home/aistudio/work/PaddleOCR/data/train_images/12536.jpg  
  inflating: /home/aistudio/work/PaddleOCR/data/train_images/823.jpg  
  inflating: /home/aistudio/work/PaddleOCR/data/train_images/15259.jpg  
  inflating

读取标签train_label.csv文件

In [45]:
import pandas as pd
%cd ~
data_label=pd.read_csv('work/PaddleOCR/data/train_label.csv', encoding='gb2312')
data_label.head()

/home/aistudio


name    value
0  0.jpg       拉拉
1  1.jpg       ６号
2  2.jpg       胖胖
3  3.jpg  前门大栅栏总店
4  4.jpg   你来就是旺季

下载预训练模型ch_ppocr_server_v2.0_rec_pre.tar

In [48]:
%cd ~/work/PaddleOCR/pre_train/
!wget https://paddleocr.bj.bcebos.com/dygraph_v2.0/ch/ch_ppocr_server_v2.0_rec_pre.tar
!tar -xf ch_ppocr_server_v2.0_rec_pre.tar


/home/aistudio/work/PaddleOCR/pre_train
--2022-10-25 12:47:47--  https://paddleocr.bj.bcebos.com/dygraph_v2.0/ch/ch_ppocr_server_v2.0_rec_pre.tar
正在解析主机 paddleocr.bj.bcebos.com (paddleocr.bj.bcebos.com)... 220.181.33.44, 220.181.33.43, 2409:8c04:1001:1002:0:ff:b001:368a
正在连接 paddleocr.bj.bcebos.com (paddleocr.bj.bcebos.com)|220.181.33.44|:443... 已连接。
已发出 HTTP 请求，正在等待回应... 200 OK
长度： 490184704 (467M) [application/x-tar]
正在保存至: “ch_ppocr_server_v2.0_rec_pre.tar”

ch_ppocr_server_v2. 100%[===================>] 467.48M  57.6MB/s    in 8.5s    

2022-10-25 12:47:55 (54.9 MB/s) - 已保存 “ch_ppocr_server_v2.0_rec_pre.tar” [490184704/490184704])



将文本全角 -> 半角，繁体 -> 简体，大写 -> 小写，删除空格，删除符号

In [4]:


import os
import cv2
from tqdm import tqdm
from langconv import Converter


def Q2B(uchar):
    """单个字符 全角转半角"""
    inside_code = ord(uchar)
    if inside_code == 0x3000:
        inside_code = 0x0020
    else:
        inside_code -= 0xfee0
    # 转完之后不是半角字符返回原来的字符
    if inside_code < 0x0020 or inside_code > 0x7e:
        return uchar
    return chr(inside_code)


def str_Q2B(ustring):
    """把字符串全角转半角"""
    return "".join([Q2B(uchar) for uchar in ustring])


def modify_ch(label):
    # 全角 -> 半角
    label = str_Q2B(label)
    # 繁体 -> 简体
    label = Converter("zh-hans").convert(label)

    # 大写 -> 小写
    label = label.lower()

    # 删除空格
    label = label.replace('　', '').replace(' ', '')

    # 删除符号
    for ch in label:
        if (not '\u4e00' <= ch <= '\u9fff') and (not ch.isalnum()):
            label = label.replace(ch, '')

    return label


def create_list():
    with open('/home/aistudio/data/data173448/train_label.csv', 'r', encoding='gbk') as f:
        lines = f.readlines()

    # 创建训练数据列表
    list_path = '/home/aistudio/work/PaddleOCR/data/train.txt'
    with open(list_path, 'w', encoding='utf-8') as f:
        for i in tqdm(range(1, 45000)):
            line = lines[i]
            path, label = str(line).replace('\n', '').split(',')
            label = modify_ch(label)
            if len(label) == 0:
                continue
            image_path = os.path.join('', path).replace('\\', '/')
            # 写入图像路径和label，用Tab隔开
            f.write(image_path + '\t' + label + '\n')

    # 创建测试数据列表
    list_path = '/home/aistudio/work/PaddleOCR/data/val.txt'
    with open(list_path, 'w', encoding='utf-8') as f:
        for i in range(45000, 50000):
            if i % 10 != 0:
                continue
            line = lines[i]
            path, label = str(line).replace('\n', '').split(',')
            label = modify_ch(label)
            if len(label) == 0:
                continue
            image_path = os.path.join('', path).replace('\\', '/')
            # 写入图像路径和label，用Tab隔开
            f.write(image_path + '\t' + label + '\n')




if __name__ == '__main__':
    create_list()
    # creat_vocabulary()

100%|██████████| 44999/44999 [00:01<00:00, 26807.04it/s]


安装需要依赖的库

In [3]:
!pip install opencv-python install "opencv-python-headless<4.3"


Looking in indexes: https://pypi.tuna.tsinghua.edu.cn/simple
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 21.6/21.6 MB 2.5 MB/s eta 0:00:0000:0100:01

[notice] A new release of pip available: 22.1.2 -> 22.3
[notice] To update, run: pip install --upgrade pip


In [2]:
!pip install scikit-image

Looking in indexes: https://pypi.tuna.tsinghua.edu.cn/simple
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 13.5/13.5 MB 3.8 MB/s eta 0:00:0000:0100:01
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 178.9/178.9 kB 4.7 MB/s eta 0:00:00a 0:00:01
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 6.4/6.4 MB 3.5 MB/s eta 0:00:0000:0100:01

[notice] A new release of pip available: 22.1.2 -> 22.3
[notice] To update, run: pip install --upgrade pip


In [3]:
!pip install --upgrade pip

Looking in indexes: https://pypi.tuna.tsinghua.edu.cn/simple
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.1/2.1 MB 4.1 MB/s eta 0:00:0000:0100:01
  Attempting uninstall: pip
    Found existing installation: pip 22.1.2
    Uninstalling pip-22.1.2:
      Successfully uninstalled pip-22.1.2


In [4]:
!pip install imgaug

Looking in indexes: https://pypi.tuna.tsinghua.edu.cn/simple
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 948.0/948.0 kB 3.9 MB/s eta 0:00:00a 0:00:01
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.0/2.0 MB 1.4 MB/s eta 0:00:0000:0100:01


In [5]:
!pip install pyclipper

Looking in indexes: https://pypi.tuna.tsinghua.edu.cn/simple
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 604.2/604.2 kB 6.1 MB/s eta 0:00:00a 0:00:01


In [6]:
!pip install lmdb

Looking in indexes: https://pypi.tuna.tsinghua.edu.cn/simple
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 298.8/298.8 kB 4.0 MB/s eta 0:00:0000:0100:01


In [7]:
!pip install rapidfuzz

Looking in indexes: https://pypi.tuna.tsinghua.edu.cn/simple
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.2/2.2 MB 6.9 MB/s eta 0:00:0000:0100:01m


cd到PaddleOCR文件夹下，开始训练，用的是mine_rec_r34_vd_none_bilstm_ctc.yml里面的配置


Global:
  use_gpu: False
  epoch_num: 300
  log_smooth_window: 20
  print_batch_step: 1
  save_model_dir: ./output/rec/r34_vd_none_bilstm_ctc2/
  save_epoch_step: 5
  # evaluation is run every 2000 iterations
  eval_batch_step: [0, 1000]
  cal_metric_during_train: True
  pretrained_model: ./pre_train/ch_ppocr_server_v2.0_rec_pre/best_accuracy
  
  
  训练300轮，算力时间不够了，没有用gpu，改成use_gpu: True 就打开gpu   预训练模型在这里设置 pretrained_model: ./pre_train/ch_ppocr_server_v2.0_rec_pre/best_accuracy


In [13]:
%cd ~/work/PaddleOCR/
!python tools/train.py -c ./configs/rec/mine_rec_r34_vd_none_bilstm_ctc.yml


/home/aistudio/work/PaddleOCR
[2022/10/26 09:34:30] ppocr INFO: Architecture : 
[2022/10/26 09:34:30] ppocr INFO:     Backbone : 
[2022/10/26 09:34:30] ppocr INFO:         layers : 34
[2022/10/26 09:34:30] ppocr INFO:         name : ResNet
[2022/10/26 09:34:30] ppocr INFO:     Head : 
[2022/10/26 09:34:30] ppocr INFO:         fc_decay : 0
[2022/10/26 09:34:30] ppocr INFO:         name : CTCHead
[2022/10/26 09:34:30] ppocr INFO:     Neck : 
[2022/10/26 09:34:30] ppocr INFO:         encoder_type : rnn
[2022/10/26 09:34:30] ppocr INFO:         hidden_size : 256
[2022/10/26 09:34:30] ppocr INFO:         name : SequenceEncoder
[2022/10/26 09:34:30] ppocr INFO:     Transform : None
[2022/10/26 09:34:30] ppocr INFO:     algorithm : CRNN
[2022/10/26 09:34:30] ppocr INFO:     model_type : rec
[2022/10/26 09:34:30] ppocr INFO: Eval : 
[2022/10/26 09:34:30] ppocr INFO:     dataset : 
[2022/10/26 09:34:30] ppocr INFO:         data_dir : ./data/train_images/
[2022/10/26 09:34:30] ppocr INFO:       

验证

In [ ]:
!python -m paddle.distributed.launch tools/eval.py -c ./configs/rec/mine_rec_r34_vd_none_bilstm_ctc.yml -o Global.checkpoints=./output/rec/r34_vd_none_bilstm_ctc/best_accuracy.pdparams


保存测试结果

In [11]:
%cd ~/work/PaddleOCR/
!python tools/infer_rec_new.py -c configs/rec/mine_rec_r34_vd_none_bilstm_ctc.yml -o Global.checkpoints=./output/rec/r34_vd_none_bilstm_ctc/best_accuracy


/home/aistudio/work/PaddleOCR
[2022/10/26 09:07:13] ppocr INFO: Architecture : 
[2022/10/26 09:07:13] ppocr INFO:     Backbone : 
[2022/10/26 09:07:13] ppocr INFO:         layers : 34
[2022/10/26 09:07:13] ppocr INFO:         name : ResNet
[2022/10/26 09:07:13] ppocr INFO:     Head : 
[2022/10/26 09:07:13] ppocr INFO:         fc_decay : 0
[2022/10/26 09:07:13] ppocr INFO:         name : CTCHead
[2022/10/26 09:07:13] ppocr INFO:     Neck : 
[2022/10/26 09:07:13] ppocr INFO:         encoder_type : rnn
[2022/10/26 09:07:13] ppocr INFO:         hidden_size : 256
[2022/10/26 09:07:13] ppocr INFO:         name : SequenceEncoder
[2022/10/26 09:07:13] ppocr INFO:     Transform : None
[2022/10/26 09:07:13] ppocr INFO:     algorithm : CRNN
[2022/10/26 09:07:13] ppocr INFO:     model_type : rec
[2022/10/26 09:07:13] ppocr INFO: Eval : 
[2022/10/26 09:07:13] ppocr INFO:     dataset : 
[2022/10/26 09:07:13] ppocr INFO:         data_dir : ./data/train_images/
[2022/10/26 09:07:13] ppocr INFO:       